In [2]:
import pandas as pd

query = """
    select  final.CUSTOMER_NUMBER_main as Focal_id,
        CAST(final.Cash_deposit_total AS DECIMAL(18, 2)) AS Cash_deposit_total,
        final.Cash_deposit_count,
        final.SEGMENT,
        final.RISK,
        final.SAR_FLAG
from 
(
    (
        select subquery.CUSTOMER_NUMBER_1 as CUSTOMER_NUMBER_main,
               subquery.Cash_deposit_total,
               subquery.Cash_deposit_count
        from 
        (
            select customer_number as CUSTOMER_NUMBER_1, 
                   sum(transaction_amount) as Cash_deposit_total, 
                   count(*) as Cash_deposit_count
            from 
            (
                select * 
                from {trans_data} trans_table 
                left join {acc_data} acc_table
                on trans_table.benef_account_number = acc_table.account_number
            ) trans
            where account_number not in ('None')
            and transaction_desc = 'CASH RELATED TRANSACTION'
            group by customer_number
        ) subquery
    ) main 
    left join 
   (
        select cd.CUSTOMER_NUMBER_3 as CUSTOMER_NUMBER_cust,
               cd.SEGMENT,
               cd.RISK,
               case
                    when ad.SAR_FLAG is NULL then 'N'
                    else ad.SAR_FLAG
               end as SAR_FLAG    
        from
        (
            select customer_number as CUSTOMER_NUMBER_3, 
                   business_segment as SEGMENT,
                   case
                       when RISK_CLASSIFICATION = 1 then 'Low Risk'
                       when RISK_CLASSIFICATION = 2 then 'Medium Risk'
                       when RISK_CLASSIFICATION = 3 then 'High Risk'
                       else 'Unknown Risk'
                   end AS RISK
            from {cust_data}
        ) cd 
        left join
        (
            select customer_number as CUSTOMER_NUMBER_4, 
                   sar_flag as SAR_FLAG
            from {alert_data}
        ) ad 
        on cd.CUSTOMER_NUMBER_3 = ad.CUSTOMER_NUMBER_4
    ) as cust_alert
    on cust_alert.CUSTOMER_NUMBER_cust = main.CUSTOMER_NUMBER_main
) as final
"""

from tms_data_interface import SQLQueryInterface

class Scenario:
    seq = SQLQueryInterface(schema="transactionschema")

    def logic(self, **kwargs):
        row_list = self.seq.execute_raw(query.format(trans_data="transaction10m",
                                                    cust_data="customer_data_v1",
                                                    acc_data="account_data_v1",
                                                    alert_data="alert_data_v1")
                                       )
        cols = ["Focal_id", "Cash_deposit_total", "Cash_deposit_count",
                "Segment", "Risk", "SAR_FLAG"]
        df = pd.DataFrame(row_list, columns = cols)
        df["Cash_deposit_total"] = df["Cash_deposit_total"].astype(float)
        return df

In [3]:
# sen = Scenario()
# sen.logic()

Focal_id  Cash_deposit_total  Cash_deposit_count           Segment  \
0     PN469304           8049952.0                 141       Mass Market   
1     PN605743           9766101.0                 175            Others   
2     PN399215           8469943.0                 164       Mass Market   
3     PN175020          17724959.0                 313            Others   
4     PN345085           7518628.0                 124            Others   
...        ...                 ...                 ...               ...   
9005  PN660329           8528178.0                 141            Others   
9006  PN336833           8475036.0                 150            Others   
9007  PN428534           7871170.0                 129  Priority Banking   
9008  PN101660           8450309.0                 142       Mass Market   
9009  PN198641           8690226.0                 166            Others   

             Risk SAR_FLAG  
0       High Risk        N  
1        Low Risk        N  
2        Low Risk        N  
3        Low Risk        N  
4     Medium Risk        N  
...           ...      ...  
9005     Low Risk        N  
9006     Low Risk        N  
9007     Low Risk        N  
9008     Low Risk        N  
9009     Low Risk        N  

[9010 rows x 6 columns]